## Daily KPI

In [0]:
select
to_char(convert_timezone('America/New_York',q.starttime),'YYYY/MM/DD'),
count(1) query_per_day,
sum(case when extract(hour from convert_timezone('America/New_York',q.starttime)) between 2 and 8 then 1 else 0 end) count_peak_hr,
sum(CASE WHEN ((total_queue_time)/1000000) > 4 THEN 1 ELSE 0 end) query_wait_gtr_4sec,
sum(case when total_queue_time>0 then 1 else 0 end) query_queue_count, -- 0 seconds decided AS 'waited in queue'
sum(case when concurrency_scaling_status=1 then 1 else 0 end) cs_query_count,
sum(case when concurrency_scaling_status>1 then 1 else 0 end) cs_invalidquery_count ,
sum(total_exec_time/60/1000000) total_exec_time_in_min,
max(total_queue_time/60/1000000) max_queue_time_in_min,
sum(total_queue_time/60/1000000) total_queue_time_in_min,
sum(case when extract(hour from convert_timezone('America/New_York',q.starttime)) between 2 and 8 then total_queue_time/60/1000000 else 0 end)
total_peak_queue_time_in_min,
sum(case when extract(hour from convert_timezone('America/New_York',q.starttime)) between 2 and 8 then total_exec_time/60/1000000 else 0 end)
total_peak_exec_time_in_min,
sum(CASE WHEN ((total_exec_time+total_queue_time)/60/1000000) > 1 THEN 1 ELSE 0 end) query_elap_time_gtr_1min,
sum(CASE WHEN ((total_exec_time+total_queue_time)/60/1000000) > 5 THEN 1 ELSE 0 end) query_elap_time_gtr_5min,
sum(CASE when ((total_exec_time+total_queue_time)/60/1000000) > 15 THEN 1 ELSE 0 end) query_elap_time_gtr15min,
sum(CASE when ((total_exec_time+total_queue_time)/60/1000000) > 15 and
extract(hour from convert_timezone('America/New_York',q.starttime)) between 2 and 8 then 1 else 0 end ) peak_query_elap_time_gtr15min,
sum(CASE when total_queue_time > 0 and
extract(hour from convert_timezone('America/New_York',q.starttime)) between 2 and 8 then 1 else 0 end ) peak_query_queue_count,
sum(CASE when total_queue_time > 300*1000000 then 1 else 0 end) q5min_queue_count,
round(sum(case when concurrency_scaling_status=1 then total_exec_time*1.0/60/1000000 else 0 end),2) cs_query_exec,
sum(CASE when total_queue_time > 60*1000000 then 1 else 0 end ) qless_1min_queue_count,
sum(CASE when total_queue_time > 900*1000000 then 1 else 0 end ) q15min_queue_count,
sum(CASE when total_queue_time > 1800*1000000 then 1 else 0 end ) q30min_queue_count
from stl_query q, stl_wlm_query ms
WHERE 1=1
AND q.query = ms.query
AND q.userid != 1
AND q.querytxt NOT LIKE 'padb%'
AND q.database = current_database()
and q.starttime > dateadd(DAY,-30,current_Date)
GROUP BY to_char(convert_timezone('America/New_York',q.starttime), 'YYYY/MM/DD')
ORDER BY 1 ;

## KPI- Track query volume to ensure optimal workload execution and minimal wait

In [0]:
select
to_char(convert_timezone('America/New_York',q.starttime),'YYYY/MM/DD'),
count(1) query_per_day,
sum(case when total_queue_time>0 then 1 else 0 end) query_queue_count, -- 0 seconds decided AS 'waited in queue'
sum(case when concurrency_scaling_status=1 then 1 else 0 end) cs_query_count,
sum(case when concurrency_scaling_status>1 then 1 else 0 end) cs_invalidquery_count ,
sum(total_exec_time/60/1000000) total_exec_time_in_min,
max(total_queue_time/60/1000000) max_queue_time_in_min,
sum(total_queue_time/60/1000000) total_queue_time_in_min,
sum(CASE when total_queue_time > 60*1000000 then 1 else 0 end ) qless_1min_queue_count,
sum(CASE when total_queue_time > 900*1000000 then 1 else 0 end ) q15min_queue_count,
sum(CASE when total_queue_time > 1800*1000000 then 1 else 0 end ) q30min_queue_count
from stl_query q, stl_wlm_query ms
WHERE 1=1
AND q.query = ms.query
AND q.userid != 1
AND q.querytxt NOT LIKE 'padb%'
AND q.database = current_database()
and q.starttime > dateadd(DAY,-30,current_Date)
GROUP BY to_char(convert_timezone('America/New_York',q.starttime), 'YYYY/MM/DD')
ORDER BY 1 ;

## Focus – Identify long running query, Frequent execution , Invalid burst queries to refactor

In [0]:
select md5(trim(left(querytxt,500))) md5qry, 
max(substring(querytxt,1,80)), max(q.query) max_queryid, 
max(q.userid),convert_timezone('America/New_York',max(starttime)) latest_time ,convert_timezone('America/New_York',min(starttime)) earliest_time,
count(1) num_queries, sum(total_exec_time/60/1000000) total_exec,sum(total_exec_time/60/1000000)/count(1) avg_exec,
max(concurrency_scaling_status) cs_status, max(service_class) service_class
from stl_query q,
stl_wlm_query w 
where q.query=w.query and concurrency_scaling_status !=1 
and q.starttime > dateadd(DAY,-7,current_Date)
group by md5(trim(left(querytxt,500))) 
having sum(total_exec_time/60/1000000)/count(1) > 1 
order by sum(total_exec_time/60/1000000) desc
limit 30;

## Identify multiple small insert calls, Frequent execution , change tobulk insert

In [0]:
select 
substring(querytxt,1,50) qrytxt,
max(w.query) query_id,
count(1) multiple_insert,
count(1)/15 avg_insert_day,
round(sum(total_exec_time*1.0/60/1000000),2) total_exec_timemin
from stl_query hsq ,
stl_wlm_query w
where w.query=hsq.query
and starttime > dateadd(DAY,-15,current_Date)
and upper(querytxt) like 'INSERT%'
group by substring(querytxt,1,50)
having count(1) > 5000 and total_exec_timemin > 100
order by 3 desc
limit 30;

## Identify  queries using nested loop with high usage

In [0]:
select md5(trim(left(querytxt,500))) md5qry, 
max(substring(querytxt,1,80)) qrytxt, max(b.query) query_id,
round(sum(total_exec_time*1.0/60/1000000),2) total_exec_timemin
from stl_query hsq ,
(select query, total_exec_time from stl_wlm_query w
where w.total_exec_time > 5*60*1000000
and w.service_class_start_time > dateadd(DAY,-15,current_Date)
and w.query in 
( select distinct query from stl_alert_event_log a
where a.event like 'Nested Loop Join%'
and event_time > dateadd(DAY,-15,current_Date) 
)
) b 
where b.query=hsq.query
and starttime > dateadd(DAY,-15,current_Date)
group by md5(trim(left(querytxt,500))) 
order by 4 desc
limit 15;

## Top burst queries

In [0]:
select md5(trim(left(querytxt,500))) md5qry, 
max(substring(querytxt,1,80)), max(q.query) max_queryid, 
max(q.userid),convert_timezone('America/New_York',max(starttime)) latest_time ,convert_timezone('America/New_York',min(starttime)) earliest_time,
count(1) num_queries, sum(total_exec_time/60/1000000) total_exec_mins,sum(total_exec_time/60/1000000)/count(1) avg_exec_mins,
max(concurrency_scaling_status) cs_status, 
max(service_class) service_class
from stl_query q,
stl_wlm_query w 
where q.query=w.query 
and concurrency_scaling_status =1 
and q.starttime > dateadd(DAY,-7,current_Date)
group by md5(trim(left(querytxt,500)))
having sum(total_exec_time/60/1000000)/count(1) > 1 
order by sum(total_exec_time/60/1000000) desc
limit 30;

## Pattern for 15 minute chunk for a day

In [0]:
select period,round(percent_queued,2),count_query,count_wait from
(
select 
to_char(convert_timezone('Est',queue_start_time),'YYMMDD-HH24') ||'-'||
mod(date_part('minute',convert_timezone('Est',queue_start_time)),4) period,
count(1) count_query,
sum(case when total_queue_time > 0 then 1 else 0 end ) count_wait,
(sum(case when total_queue_time > 0 then 1 else 0 end)/count(query)::decimal)*100 as percent_queued
from
STL_WLM_QUERY
where
userid != 1
and date_trunc('day', convert_timezone('Est', queue_start_time)) = '2023-07-10'
-- and total_queue_time > 0
group by to_char(convert_timezone('Est', queue_start_time),'YYMMDD-HH24') ||'-'||
mod(date_part('minute',convert_timezone('Est', queue_start_time)),4)
)
order by 1;

## Concurrency scaling usage
- If this table is not included in persist utility, please consider to back this up

In [0]:
select to_char(start_time,'YYYYMMDD'),sum(queries) cs_query_per_day,sum(usage_in_seconds) ,
to_char(max(end_time),'YYYYMMDD') 
from svcs_concurrency_scaling_usage 
group by 1 order by 1;

## Queue Time

In [0]:
select
 trunc(service_class_start_time)
, service_class
, count( query) as cnt_query
, sum(total_queue_time/60000000) as total_queue_time
, max(total_queue_time/60000000) as max_queue_time
,sum(total_exec_time/60000000) as total_exec_time
,max(total_exec_time/60000000) as max_exec_time
, PERCENTILE_CONT(.99) within group (order by (total_exec_time+total_queue_time)/60000000) as P99
, PERCENTILE_CONT(1) within group (order by (total_exec_time+total_queue_time)/60000000) as P100
from STL_WLM_QUERY
where trunc(service_class_start_time) > '2023-04-02'
and service_class in (102,105)
group by 1,2
UNION ALL
select 
 trunc(service_class_start_time)
, service_class
, count( query) as cnt_query
, sum(total_queue_time/60000000) as total_queue_time
, max(total_queue_time/60000000) as max_queue_time
,sum(total_exec_time/60000000) as total_exec_time
,max(total_exec_time/60000000) as max_exec_time
, PERCENTILE_CONT(.99) within group (order by (total_exec_time+total_queue_time)/60000000) as P99
, PERCENTILE_CONT(1) within group (order by (total_exec_time+total_queue_time)/60000000) as P100
from STL_WLM_QUERY
where trunc(service_class_start_time) between '2023-03-01' and '2023-04-02' 
and service_class in (102,105)
group by 1,2
order by 2,1;

## compile time
- if svl compile is not being backed up, you can include in your persist table stored procedure

In [0]:
SELECT TO_CHAR(CONVERT_TIMEZONE('America/New_York', starttime),'YYYY/MM/DD')
, COUNT( query) AS cnt_query 
, SUM(DATEDIFF(us,starttime,endtime)) AS total_compile_time
FROM svl_compile
WHERE compile = 1
AND userid <> 1 
GROUP BY  1 
ORDER BY 1;

## Concurrency Scaling Status code

In [0]:
select
to_char(convert_timezone('America/New_York',q.starttime),'YYYY/MM/DD'),
CASE WHEN concurrency_scaling_status = 1 THEN 'Ran on a Concurrency Scaling cluster'
       WHEN concurrency_scaling_status = 0 THEN 'Ran on the main cluster'
       WHEN concurrency_scaling_status = 2
         THEN 'Concurrency Scaling not enabled'
       WHEN concurrency_scaling_status = 4
         THEN 'Concurrency Scaling ineligible query - '
         'System temporary table accessed'
       WHEN concurrency_scaling_status = 5
         THEN 'Concurrency Scaling ineligible query - '
         'User temporary table accessed'
       WHEN concurrency_scaling_status = 6
         THEN 'Concurrency Scaling ineligible query - System table accessed'
       WHEN concurrency_scaling_status = 3
         THEN 'Concurrency Scaling ineligible query - Query is an Unsupported'
         ' DML'
       WHEN concurrency_scaling_status = 7
         THEN 'Concurrency Scaling ineligible query - '
         'No backup table accessed'
       WHEN concurrency_scaling_status = 8
         THEN 'Concurrency Scaling ineligible query - '
         'Zindex table accessed'
       WHEN concurrency_scaling_status = 9
         THEN 'Concurrency Scaling ineligible query - Query uses UDF'
       WHEN concurrency_scaling_status = 10
         THEN 'Concurrency Scaling ineligible query - Catalog tables accessed'
       WHEN concurrency_scaling_status = 11
         THEN 'Concurrency Scaling ineligible query - Dirty table accessed'
       WHEN concurrency_scaling_status = 12
         THEN 'Concurrency Scaling ineligible query - Direct dispatched query'
       WHEN concurrency_scaling_status = 16
         THEN 'Concurrency Scaling ineligible query - No tables accessed'
       WHEN concurrency_scaling_status = 17
         THEN 'Concurrency Scaling ineligible query - Spectrum queries are '
         'disabled'
       WHEN concurrency_scaling_status = 18
         THEN 'Concurrency Scaling ineligible query - Function not supported '
       WHEN concurrency_scaling_status = 19
         THEN 'Concurrency Scaling ineligible query - Instance type not supported '
       WHEN concurrency_scaling_status = 20
         THEN 'Concurrency Scaling ineligible query - Burst temporarily disabled '
       WHEN concurrency_scaling_status = 21
         THEN 'Concurrency Scaling ineligible query - Unload queries are disabled '
       WHEN concurrency_scaling_status = 22
         THEN 'Concurrency Scaling ineligible query - Unsupported unload type '
       WHEN concurrency_scaling_status = 23
         THEN 'Concurrency Scaling ineligible query - Non VPC clusters cannot burst '
       WHEN concurrency_scaling_status = 24
         THEN 'Concurrency Scaling ineligible query - VPCE not setup '
       WHEN concurrency_scaling_status = 25
         THEN 'Concurrency Scaling failed query - Inelegible to rerun on main cluster due to failure handling not enabled'
       WHEN concurrency_scaling_status = 26
         THEN 'Concurrency Scaling failed query - Inelegible to rerun on main cluster due to concurrency scaling not auto'
       WHEN concurrency_scaling_status = 27
         THEN 'Concurrency Scaling failed query - Inelegible to rerun on main cluster due to results already returning '
       WHEN concurrency_scaling_status = 28
         THEN 'Concurrency Scaling failed query - Inelegible to rerun on main cluster due to non retriable error '
       WHEN concurrency_scaling_status = 29
         THEN 'Concurrency Scaling failed query - Elegible to rerun on main cluster '
       WHEN concurrency_scaling_status = 30
         THEN 'Concurrency Scaling inelegible query - Cumulative time not met '
       WHEN concurrency_scaling_status = 31
         THEN 'Concurrency Scaling inelegible query - Paused query '
       WHEN concurrency_scaling_status = 32
         THEN 'Query assigned to non Concurrency Scaling queue '
       WHEN concurrency_scaling_status = 33
         THEN 'Concurrency Scaling ineligible query - Query has state on Main cluster '
       WHEN concurrency_scaling_status = 34
         THEN 'Concurrency Scaling ineligible query - Query is inelegible for bursting Volt CTAS '
       WHEN concurrency_scaling_status = 35
         THEN 'Concurrency Scaling ineligible query - Resource blacklisted '
       WHEN concurrency_scaling_status = 36
         THEN 'Concurrency Scaling ineligible query - Non-retryable VoltTT queries are blacklisted '
       WHEN concurrency_scaling_status = 37
         THEN 'Concurrency Scaling ineligible query - Query is retrying on Main cluster '
       WHEN concurrency_scaling_status = 38
         THEN 'Concurrency Scaling ineligible query - Cannot burst Volt-created CTAS using cursors '
       WHEN concurrency_scaling_status = 39
         THEN 'Concurrency Scaling usage limit reached '
       WHEN concurrency_scaling_status = 40
         THEN 'Concurrency Scaling ineligible query - Unsupported VoltTT Utility query '
       WHEN concurrency_scaling_status = 41
         THEN 'Concurrency Scaling ineligible query - Write query generating Volt TTs '
       WHEN concurrency_scaling_status = 42
         THEN 'Concurrency Scaling ineligible query - VoltTT query with invalid state '
       WHEN concurrency_scaling_status = 43
         THEN 'Concurrency Scaling ineligible query - Explain query generating Volt TTs '
       WHEN concurrency_scaling_status = 44
         THEN 'Concurrency Scaling ineligible query - Bursting Volt-generated queries is disabled '
       WHEN concurrency_scaling_status = 45
         THEN 'Concurrency Scaling ineligible query - Resource of VoltTT UNLOAD is blacklisted '
       WHEN concurrency_scaling_status = 46
         THEN 'Concurrency Scaling ineligible query - Multiple pre-Volt query trees '
       WHEN concurrency_scaling_status = 48
         THEN 'Concurrency Scaling ineligible query - Target table is DistAll/DistAutoAll '
       WHEN concurrency_scaling_status = 49
         THEN 'Concurrency Scaling ineligible query - Table that has diststyle changed in current txn accessed '
       WHEN concurrency_scaling_status = 50
         THEN 'Concurrency Scaling ineligible query - Cannot burst spectrum copy '
       WHEN concurrency_scaling_status = 51
         THEN 'Concurrency Scaling ineligible query - Dirty transaction tables accessed  '
       WHEN concurrency_scaling_status = 52
         THEN 'Concurrency Scaling ineligible query - Table that has identity column as a target table '
       WHEN concurrency_scaling_status = 53
         THEN 'Concurrency Scaling ineligible query - Datasharing remote tables accessed'
       WHEN concurrency_scaling_status = 54
         THEN 'Concurrency Scaling ineligible query - Target table with comp update'
       WHEN concurrency_scaling_status = 55
         THEN 'Concurrency Scaling ineligible query - Nested tables accessed'
       WHEN concurrency_scaling_status = 56
         THEN 'Concurrency Scaling ineligible query - Copy from EMR '
       WHEN concurrency_scaling_status = 59
         THEN 'Concurrency Scaling ineligible query - Table that has column encode changed in current txn accessed '
       WHEN concurrency_scaling_status = 60
         THEN 'Concurrency Scaling ineligible query - MV refresh disabled '
       WHEN concurrency_scaling_status = 61
         THEN 'Concurrency Scaling ineligible query - Too many concurrent writes '
       WHEN concurrency_scaling_status = 62
         THEN 'Concurrency Scaling ineligible query - Main cluster too big for writes '
       WHEN concurrency_scaling_status = 63
         THEN 'Concurrency Scaling ineligible query - Datasharing VoltTT '
       WHEN concurrency_scaling_status = 64
         THEN 'Concurrency Scaling ineligible query - Target table has super/geo column '
       WHEN concurrency_scaling_status = 65
         THEN 'Concurrency Scaling rejected query - Ineligible to queue on burst cluster, eligible to rerun on any cluster '
       WHEN concurrency_scaling_status = 66
         THEN 'Concurrency Scaling ineligible query - Datasharing with burst-write'
       WHEN concurrency_scaling_status = 67
         THEN 'Concurrency Scaling ineligible query - CTAS with burst-write'
       WHEN concurrency_scaling_status = 68
         THEN 'Concurrency Scaling ineligible query - COPY on tables with identity columns'
       WHEN concurrency_scaling_status = 70
         THEN 'Concurrency Scaling ineligible query - Datasharing query with cursor'
       ELSE 'Concurrency Scaling ineligible query - Unknown status'
       END as concurrency_scaling_status_txt,
count(1) query_per_day

from stl_query q, stl_wlm_query ms
WHERE 1=1
AND q.query = ms.query
AND q.userid != 1
AND q.querytxt NOT LIKE 'padb%'
AND q.database = current_database()
and q.starttime > dateadd(DAY,-30,current_Date)
GROUP BY to_char(convert_timezone('America/New_York',q.starttime), 'YYYY/MM/DD'), 2
ORDER BY 1 ;